In [1]:
import numpy as np
from tensorflow import keras
from tensorflow.keras import layers
import tensorflow as tf

## Setup training/test data

In [2]:
import tensorflow_datasets as tfds
import tensorflow as tf
ds, info = tfds.load('imagenet_v2', split='test', shuffle_files=False, with_info=True)
print(info.features)
num_classes = info.features['label'].num_classes
input_shape = info.features['image'].shape
ds = ds.take(2000)
x_test = np.asarray([tf.keras.applications.inception_v3.preprocess_input(tf.keras.layers.Resizing(299, 299)(v['image'])) for v in ds])
y_test_l = np.asarray([tfds.as_numpy(v['label']) for v in ds])
model = tf.keras.applications.InceptionV3(include_top=False, weights='imagenet')
model.summary()

FeaturesDict({
    'file_name': Text(shape=(), dtype=tf.string),
    'image': Image(shape=(None, None, 3), dtype=tf.uint8),
    'label': ClassLabel(shape=(), dtype=tf.int64, num_classes=1000),
})
Model: "inception_v3"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_1 (InputLayer)           [(None, None, None,  0           []                               
                                 3)]                                                              
                                                                                                  
 conv2d (Conv2D)                (None, None, None,   864         ['input_1[0][0]']                
                                32)                                                               
                                                                                         

## MNIST 

In [2]:
import tensorflow_datasets as tfds
ds, info = tfds.load('mnist', split='test', shuffle_files=False, batch_size=-1, with_info=True)
print(info.features['label'].num_classes)
num_classes = info.features['label'].num_classes
input_shape = info.features['image'].shape
x_test = tfds.as_numpy(ds['image']).astype("float32")  / 255
y_test_l = tfds.as_numpy(ds['label'])

# Load pretrained model
model_save_name = 'mnist_classifier'
path = F"{model_save_name}" 
#model.save(path)
model = keras.models.load_model(path)
print(type(model))
model.summary()

10
<class 'keras.engine.sequential.Sequential'>
Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv2d (Conv2D)             (None, 26, 26, 32)        320       
                                                                 
 max_pooling2d (MaxPooling2D  (None, 13, 13, 32)       0         
 )                                                               
                                                                 
 conv2d_1 (Conv2D)           (None, 11, 11, 64)        18496     
                                                                 
 max_pooling2d_1 (MaxPooling  (None, 5, 5, 64)         0         
 2D)                                                             
                                                                 
 flatten (Flatten)           (None, 1600)              0         
                                                                 
 dropout

## Compute network layer activations for each image

In [3]:
%reload_ext autoreload
%autoreload 2

import nap
ap = nap.NeuralActivationPattern(x_test[:2000], y_test_l[:2000], model)

In [4]:
def show_image_grid(images, labels, img_idx, title, images_per_row, img_scale):
    import plotly.express as px
    if images[0].shape[2] > 1:
        imSize = (images[0].shape[0], images[0].shape[1], images[0].shape[2])
    else:
        imSize = (images[0].shape[0], images[0].shape[1])
    # Get indices of the largest 
    sampleSize = len(img_idx)
    nCols = min(sampleSize, images_per_row)
    nRows =  1 +sampleSize % images_per_row
    img = np.array([images[idx].reshape(imSize) for idx in img_idx])
    fig = px.imshow(img, facet_col=0, binary_string=True, facet_col_wrap=nCols, 
                    #width=int(nCols*imSize[0]*img_scale), 
                    #height=50+int(nRows*10 + nRows*imSize[1]*img_scale), 
                    title=title
                    )
    # Set facet titles
    for i, im in enumerate(img_idx):
        fig.layout.annotations[i]['text'] = f"{labels[im]}"
    #fig.update_yaxes(automargin=False, title=title)
    #fig.update_xaxes(automargin=True)
    fig.update_layout(margin=dict(b=0))
    #fig.update_annotations(standoff=10)
    fig.show()

def show_pattern(average, representatives, outliers, images, labels, title):
    import plotly.express as px
    import plotly.subplots as sp
    if images[0].shape[2] > 1:
        imSize = (images[0].shape[0], images[0].shape[1], images[0].shape[2])
    else:
        imSize = (images[0].shape[0], images[0].shape[1])
    img = np.array([average.reshape(imSize)] + [images[idx].reshape(imSize) for idx in representatives] + [images[idx].reshape(imSize) for idx in outliers])
    fig = px.imshow(img, facet_col=0, binary_string=True, title = title)
    fig.layout.annotations[0]['text'] = "Average"
    for i, im in enumerate(representatives):
        fig.layout.annotations[1+i]['text'] = f"Representative | {labels[im]}"
    for i, im in enumerate(outliers):
        fig.layout.annotations[len(representatives)+1+i]['text'] = f"Outlier | {labels[im]}"
    fig.show()

def show_images(images, labels, layer_img_idx, titles, images_per_row = 10, img_scale = 7.0):
    for layer, img_idx in enumerate(layer_img_idx):
        show_image_grid(images, labels, img_idx, titles[layer], images_per_row, img_scale)


## Show the images generating highest activations for each layer

In [8]:
max_activations = [ap.layer_max_activations(layerId, agg_func = np.average) for layerId in range(len(model.layers))]
titles = [f"Highest activating images for layer {layerId}" for layerId in range(len(max_activations))]
show_images(x_test, y_test_l, max_activations, titles)

# Neural Activation Patterns

In [7]:
nSamplesPerLayer = 10
layerId = "mixed3"

### Show overview of patterns with respect to output data (y) 

In [8]:
%reload_ext autoreload
%autoreload 2

import nap
ap.layer_summary(layerId)

Layer 100, number of patterns: 2


## Show inputs treated the same way by the network

In [11]:
#sorted_patterns = ap.sorted(layerId)

for pattern_id, pattern in sorted_patterns.groupby('patternId'):
    avg = ap.average(pattern.index)
    centers = pattern.head(5).index
    outliers = pattern.tail(3).index
    show_pattern(avg, centers, outliers, x_test, y_test_l, F"Layer {layerId}, Pattern: {pattern_id}, Size: {len(pattern)}")

### Filter-level

In [19]:
layerId = 3
filterId = 1
sorted_patterns = nap.sort(ap.filter_patterns(layerId, filterId))

for pattern_id, pattern in sorted_patterns.groupby('patternId'):
    avg = ap.average(pattern.index)
    centers = pattern.head(1).index
    outliers = pattern.tail(3).index
    show_pattern(avg, centers, outliers, x_test, y_test_l, F"Layer {layerId}, Filter: {filterId}, Pattern: {pattern_id}, Size: {len(pattern)}")

Layer 3, filter: 1, number of patterns: 8


In [20]:

frac = 0.1
pattern_samples = ap.head(layerId, nSamplesPerLayer) 
titles = []
patterns = []
for pattern_id, pattern in pattern_samples.groupby('patternId'):
    patterns.append(pattern.index)
    titles.append(F"Layer {layerId}, Pattern: {pattern_id} - Images most likely belonging to pattern")
show_images(x_test, y_test_l, patterns, titles)

Layer 3, number of patterns: 10


### Show aggregated inputs treated the same way 

In [21]:
for layerId, layer in enumerate(model.layers):
    averages = []
    pattern_labels = []
    for pattern_id, pattern in ap.layer_patterns(layerId).groupby('patternId'):
        averages.append(ap.average(pattern.index))
        pattern_labels.append(f"Id: {pattern_id}, Size: {len(pattern)}")
    nPatterns = len(averages)
    indices = list(range(nPatterns))
    show_images(averages, pattern_labels, [indices], [f"Layer {layerId} - Pattern averages"])

Layer 0, number of patterns: 2


Layer 1, number of patterns: 2


Layer 2, number of patterns: 7


Layer 3, number of patterns: 10


Layer 4, number of patterns: 10


Layer 5, number of patterns: 10


Layer 6, number of patterns: 11



### Show activation for each feature. Warning!!! slow code. 

In [ ]:

# Convert to slow, but plotting friendly pandas DataFrame
activations_df = {'input_data': [], 'layer': [], 'feature': [], 'activation':[]}
for dp in range(len(layer_activations)):
  for feature in range(len(ap.layer_activations[0])):
      for activation in layer_activations[:][feature]:
        activations_df['input_data'].append(dp)
        activations_df['layer'].append(patternOnLayer)
        activations_df['feature'].append(feature)
        activations_df['activation'].append(activation)

activations_df = pd.DataFrame(activations_df)
activations_df.describe()

In [ ]:
px.scatter(activations_df, x='feature', y='activation')